In [1]:
import random 
import gym
import numpy as np 
from collections import deque
import tensorflow as tf 
import tflearn as tl 
from tflearn.activations import softmax

Instructions for updating:
Colocations handled automatically by placer.


In [2]:
episode_infos = {'run' : [], 'step' : [], 'total_reward' : [], 'avg_reward' : []}

In [3]:
def cartpole():
    env = gym.make('CartPole-v1')
    observation_space = env.observation_space.shape[0]
    action_space = env.action_space.n
    sess = tf.InteractiveSession()
    a3c_solver = A3CSolver(observation_space, action_space, sess)
    sess.run(tf.global_variables_initializer())
    #a3c_solver.model.load_weights('dqn_weights_%i.h5' % (prev_stop))
    run = 0
    while True:
    #for _ in range(300):
        run += 1
        state = env.reset()
        state = np.reshape(state, [1, observation_space])
        step = 0
        total_reward = 0
        while True:
            step += 1
            action = a3c_solver.act(state)
            state_next, reward, terminal, info = env.step(action)
            reward = reward if not terminal else -reward
            total_reward += reward
            state_next = np.reshape(state_next, [1, observation_space])
            a3c_solver.remember(state, action, reward, state_next, terminal)
            state = state_next
            if terminal:
                
                episode_infos['run'].append(run)
                episode_infos['step'].append(step)
                episode_infos['total_reward'].append(total_reward)
                episode_infos['avg_reward'].append(total_reward / step)
                
                print('epsilon : ' + str(a3c_solver.exploration_rate))
                print('run : ' + str(run) + ' score : ' + str(total_reward) + ' avg_score : ' + str(total_reward / step))
                break
            a3c_solver.experience_replay()
        #dqn_solver.model.save_weights('dqn_weights_%i.h5' % (run))

### Loss function : 
$$L= L_\pi + \alpha L_Q + \beta L_{reg}$$
### Policy loss :
$$A = (R - Q_{a_i\sim \pi}(a_i,s_i; \theta'_q))$$
$$\frac{\partial\,J(\pi)}{\partial\, \theta'} = \frac{1}{n}\sum_{i=1}^{n}\frac{\partial\,log\,\pi (a_i|s_i;\theta')}{\partial\,\theta'}\; A$$
$$\therefore J(\pi) = \frac{1}{n}\sum_{i=1}^{n}log\,\pi (a_i|s_i;\theta')\; A\;\;\;\;\;\;[\because A\;is\;considered\;constant]$$
∵ We want to maximize 𝐽(𝜋) $$L_\pi = -J(\pi)$$
### Value loss :
$$J(Q) = \sum_{i=1}^{n}(R - Q_{a_i\sim \pi}(a_i,s_i; \theta'_q))$$
$$L_Q = J(Q)$$
### Policy entropy :
$$H(\overrightarrow{\pi(s)})=-\sum_{i=1}^{n}\sum_{k=1}^{m} \pi(s_i)_k\cdot log\, \pi(s_i)_k$$
$$L_{reg}=H(\overrightarrow{\pi(s)})$$

In [4]:
y = 0.95
l_rate = 0.0001

exp_memory_size = 1000000
batch_size = 20

exploration_max = 1.0
exploration_min = 0.01
exploration_decay = 0.9995

alpha = 0.5
beta = 0.01

In [5]:
class A3CSolver():
    def __init__(self, observation_space, action_space, sess):
        self.sess = sess
        self.exploration_rate = exploration_max
        self.action_space = action_space
        self.memory = deque(maxlen = exp_memory_size)
        
        self.state = tl.input_data(shape = [None, observation_space], name = 'S_i')
        #self.action = tl.input_data(shape = [None, action_space], name = 'A_i')
        self.R = tl.input_data(shape = [None, 1], name = 'R_i')
        
        #Actor 𝜋(a_i|s_i;𝜃′)
        self.actor = self.build_actor(self.state, action_space)
        #Critic Q_a_i∼𝜋(a_i,s_i;𝜃′_q)
        self.critic = self.build_critic(self.state) #, self.action)
        
        #Loss L
        self.loss = self.compute_loss()
        #Optimize ops 
        self.opt = tf.train.AdamOptimizer(learning_rate = l_rate).minimize(self.loss)
        
    def build_actor(self, state_input, action_space):
        #State input s_i
        a_h1 = tl.fully_connected(state_input, 24)        
        a_h2 = tl.fully_connected(a_h1, 48)        
        a_logit = tl.fully_connected(a_h2, action_space)
        return softmax(a_logit)
    
    def build_critic(self, state_input):#, action_input):
        #Action input a_i
        #as_h1 = tl.fully_connected(action_input, 24)
        #as_h2 = tl.fully_connected(as_h1, 48)
        #State input s_i
        ss_h1 = tl.fully_connected(state_input, 24)
        ss_h2 = tl.fully_connected(ss_h1, 48)
        #Combine state action input 
        #q_h1 = tl.layers.merge_ops.merge([as_h2, ss_h2], mode = 'elemwise_sum')
        return tl.fully_connected(ss_h2, 1)
    
    def remember(self, state, action, reward, state_next, done):
        self.memory.append([state, action, reward, state_next, done])
        
    def act(self, state, infer = False):
        #act
        if not infer and np.random.rand() < self.exploration_rate:
            return random.randrange(self.action_space)
        action = self.sess.run(self.actor, feed_dict = {self.state : state})
        return np.argmax(action[0])
    
    def experience_replay(self):
        if len(self.memory) < batch_size:
            return
        batch = random.sample(self.memory, batch_size)
        for state, action, reward, state_next, done in batch:
            R = np.array(reward).reshape([1, 1])
            action = np.identity(2)[action].reshape([1, self.action_space])
            if not done:
                action_next = self.sess.run(self.actor, feed_dict = {self.state : state_next})
                R = reward + y * self.sess.run(self.critic, feed_dict = {self.state : state_next, self.action : action_next})
            #Optimize
            loss, _, a, b, c= self.sess.run([self.loss, self.opt, self.L_pi, self.L_v, self.actor], feed_dict = {self.state : state, 
                                                                        self.action : action, 
                                                                        self.R : R})
            print(loss, a, b, c)
            self.exploration_rate *= exploration_decay
            self.exploration_rate = max(exploration_min, self.exploration_rate)

    def compute_loss(self):
        #Advantage
        A = self.R - self.critic
        #Policy loss 
        self.L_pi = - tf.reduce_mean(tf.reduce_mean(tf.log(self.actor + 1e-13) * A, axis = -1))
        #Value loss
        self.L_v = tf.reduce_mean(tf.math.square(A))
        #Policy entropy 
        self.L_reg = tf.reduce_mean(tf.reduce_sum(tf.multiply(self.actor, tf.log(self.actor + 1e-13)), axis = -1))
        #Total loss 
        return self.L_pi + alpha * self.L_v #+ beta * self.L_reg 

In [6]:
cartpole()

Instructions for updating:
Use tf.cast instead.
epsilon : 1.0
run : 1 score : 7.0 avg_score : 0.7777777777777778
1.1927538 0.69298613 0.9995354 [[0.49996993 0.5000301 ]]
1.1935587 0.6933157 1.0004861 [[0.500018 0.499982]]
1.192626 0.6929338 0.9993844 [[0.50006205 0.49993798]]
-0.19295436 -0.6935823 1.0012559 [[0.4999689 0.5000311]]
1.1935627 0.6933173 1.000491 [[0.49999666 0.50000334]]
1.1935519 0.6933129 1.000478 [[0.4999191 0.5000809]]
1.19354 0.693308 1.000464 [[0.49993658 0.5000634 ]]
1.1935302 0.69330394 1.0004525 [[0.49999866 0.5000014 ]]
1.1935098 0.6932956 1.0004284 [[0.50002027 0.49997976]]
1.1934792 0.6932831 1.0003922 [[0.5000121  0.49998793]]
1.1934556 0.6932734 1.0003643 [[0.50002515 0.49997488]]
1.192344 0.6928183 0.9990512 [[0.5000314 0.4999686]]
1.1934047 0.69325256 1.0003042 [[0.5000234 0.4999766]]
1.1933763 0.69324094 1.0002706 [[0.49999577 0.50000423]]
1.1933563 0.6932328 1.000247 [[0.49999955 0.5000004 ]]
1.193335 0.69322413 1.000222 [[0.5 0.5]]
1.1922164 0.6927661 

-0.1430583 -0.7860172 1.2859178 [[0.5000073  0.49999276]]
1.1887581 0.691349 0.9948183 [[0.5000033  0.49999672]]
1.1894339 0.691626 0.9956158 [[0.5000087  0.49999133]]
1.1883689 0.6911894 0.994359 [[0.4999999  0.50000006]]
1.1893965 0.6916107 0.9955716 [[0.5000028  0.49999723]]
1.18929 0.69156706 0.9954459 [[0.5000005  0.49999955]]
1.1877451 0.6909336 0.9936231 [[0.4999957 0.5000043]]
1.1880269 0.6910491 0.9939555 [[0.49999514 0.5000049 ]]
1.1883541 0.6911833 0.99434155 [[0.49999657 0.50000346]]
1.1873302 0.69076335 0.99313366 [[0.4999974 0.5000026]]
1.1868111 0.69055045 0.9925212 [[0.5000022  0.49999776]]
1.1886867 0.6913197 0.9947341 [[0.5000069  0.49999312]]
1.1868533 0.69056773 0.9925711 [[0.5000096  0.49999043]]
1.1752508 0.6857977 0.9789063 [[0.4999995  0.50000054]]
1.1757473 0.68600214 0.9794902 [[0.49999687 0.50000316]]
1.188791 0.6913625 0.99485713 [[0.4999889 0.5000111]]
1.1751615 0.68576086 0.9788013 [[0.49999633 0.5000037 ]]
1.1856799 0.69008625 0.9911873 [[0.49999955 0.500

1.0729743 0.6428736 0.86020154 [[0.49999037 0.5000096 ]]
1.1672689 0.6825048 0.96952814 [[0.5000058 0.4999942]]
1.0641404 0.63908887 0.8501032 [[0.5000002  0.49999985]]
1.1678848 0.6827592 0.9702513 [[0.50000215 0.49999785]]
1.2891233 -1.6927075 5.9636617 [[0.50001186 0.49998817]]
1.0557733 0.63549227 0.84056187 [[0.50002486 0.49997517]]
1.168256 0.68291247 0.97068703 [[0.5000274 0.4999726]]
1.1830544 0.68900806 0.9880928 [[0.50000846 0.49999157]]
1.1857885 0.6901308 0.9913155 [[0.49998835 0.5000117 ]]
1.1690719 0.6832494 0.97164494 [[0.49999663 0.50000334]]
1.1775215 0.68673277 0.98157746 [[0.49998376 0.5000162 ]]
1.1699612 0.6836165 0.9726894 [[0.49999294 0.5000071 ]]
1.1664181 0.6821532 0.96852976 [[0.4999964  0.50000364]]
1.0466311 0.63154936 0.8301634 [[0.50001013 0.49998984]]
1.1636783 0.68102044 0.96531576 [[0.50001866 0.49998137]]
1.1618036 0.6802447 0.9631179 [[0.50000197 0.49999806]]
1.0560086 0.6355936 0.84082985 [[0.49998912 0.5000109 ]]
1.1826707 0.6888504 0.98764056 [[0.4

0.9134004 0.5724132 0.6819745 [[0.5002306  0.49976936]]
1.1118896 0.6593964 0.9049865 [[0.5002843  0.49971575]]
0.88535976 0.55953866 0.6516422 [[0.50015384 0.49984616]]
1.1104302 0.65878105 0.90329844 [[0.5001761  0.49982396]]
1.1051455 0.65655005 0.8971907 [[0.500071   0.49992898]]
1.0981649 0.6535965 0.88913673 [[0.5000436  0.49995643]]
1.0732181 0.64297783 0.8604805 [[0.5000455 0.4999545]]
1.1201136 0.66285765 0.91451204 [[0.49972007 0.50027996]]
0.92081165 0.5757898 0.69004375 [[0.49953708 0.50046295]]
1.0804257 0.64605606 0.8687394 [[0.49986833 0.5001317 ]]
1.0983924 0.65369296 0.8893989 [[0.4998295  0.50017047]]
0.8944446 0.5637273 0.6614346 [[0.49967086 0.50032914]]
1.0589758 0.63687027 0.84421116 [[0.5000782  0.49992183]]
0.8580159 0.54682875 0.62237436 [[0.4998904 0.5001096]]
1.0816648 0.6465844 0.8701609 [[0.5000693 0.4999307]]
1.1297884 0.666916 0.9257447 [[0.49983343 0.50016654]]
0.83894575 0.53787065 0.60215014 [[0.5001203  0.49987972]]
7.6025167 -3.225656 21.656345 [[0.5

0.8349414 0.5359796 0.59792346 [[0.5000576 0.4999424]]
1.062885 0.63855004 0.8486701 [[0.4998827 0.5001173]]
1.0185282 0.6193402 0.7983761 [[0.5001742 0.4998258]]
0.75458455 0.4972589 0.51465124 [[0.5007028  0.49929723]]
1.0389767 0.62823725 0.8214788 [[0.4998804  0.50011957]]
0.9430754 0.58586925 0.71441233 [[0.5007825 0.4992175]]
0.7952396 0.51703674 0.5564058 [[0.50028753 0.49971244]]
0.81532973 0.5266669 0.5773257 [[0.5002111  0.49978882]]
0.82721925 0.5323229 0.5897927 [[0.49997407 0.5000259 ]]
0.959393 0.5931961 0.7323939 [[0.5006127  0.49938735]]
0.8441608 0.5403282 0.60766524 [[0.4999726 0.5000274]]
0.98714244 0.60554254 0.76319987 [[0.49997857 0.5000214 ]]
0.95259726 0.59015065 0.72489315 [[0.5006009  0.49939916]]
0.93804103 0.5835984 0.7088853 [[0.50069714 0.49930283]]
0.9816371 0.60310423 0.7570658 [[0.50032413 0.4996759 ]]
0.94100356 0.58493507 0.712137 [[0.5006036  0.49939638]]
1.0537081 0.6346029 0.8382104 [[0.49974248 0.5002575 ]]
0.999789 0.6111231 0.7773319 [[0.4999806

...

-111.951744 -219.23161 214.55974 [[0. 1.]]
-111.8582 -215.96196 208.20752 [[0. 1.]]
-108.603516 -263.02863 308.85022 [[1. 0.]]
-110.16742 -195.33145 170.32806 [[0. 1.]]
-111.60166 -210.60268 198.00203 [[0. 1.]]
-111.65238 -211.47906 199.65337 [[0. 1.]]
-110.219475 -195.74104 171.04314 [[0. 1.]]
-103.016304 -160.5548 115.07698 [[1. 0.]]
-111.99731 -225.54596 227.0973 [[0. 1.]]
-102.11131 -157.43645 110.65027 [[1. 0.]]
-71.29023 -88.95126 35.32207 [[0. 1.]]
-106.01903 -172.22969 132.42133 [[1. 0.]]
-71.747444 -89.711754 35.928623 [[0. 1.]]
-111.84237 -232.47783 241.27092 [[2.2779096e-21 1.0000000e+00]]
2071.9683 -869.6262 5883.189 [[1.4186144e-10 1.0000000e+00]]
-102.25871 -157.93431 111.35119 [[1. 0.]]
-111.9855 -226.77324 229.57549 [[0. 1.]]
-66.318016 -80.94169 29.247341 [[0. 1.]]
2737.5186 -1353.8793 8182.796 [[1. 0.]]
-14.178457 -14.65804 0.9591658 [[0. 1.]]
-111.98936 -226.44165 228.90459 [[0. 1.]]
-98.21803 -145.42003 94.403984 [[1.0000000e+00 2.4896937e-21]]
-110.399536 -197.2061

4.5325623 -32.828365 74.721855 [[9.9949706e-01 5.0296990e-04]]
-90.70831 -126.33196 71.24729 [[1.000000e+00 6.736023e-32]]
-111.298355 -206.24265 189.88858 [[0. 1.]]
-69.55683 -86.10616 33.09866 [[0. 1.]]
-9.311546 -42.934273 67.24545 [[9.9997163e-01 2.8337603e-05]]
-101.68634 -156.02144 108.67019 [[1. 0.]]
2695.712 -1345.56 8082.544 [[0. 1.]]
-97.49321 -143.3804 91.77439 [[1. 0.]]
-87.26277 -118.726036 62.926537 [[2.8564739e-36 1.0000000e+00]]
-112.00127 -224.77792 225.55331 [[0. 1.]]
-72.89929 -91.64701 37.49544 [[0. 1.]]
-95.16768 -137.15924 83.983116 [[1. 0.]]
-86.15383 -116.39239 60.477108 [[1.444305e-26 1.000000e+00]]
-92.06052 -129.484 74.84695 [[1.0000000e+00 1.2343362e-37]]
-96.53076 -140.7493 88.437065 [[1. 0.]]
-111.24725 -242.40097 262.30743 [[0. 1.]]
-110.84743 -246.75449 271.81412 [[8.1634995e-25 1.0000000e+00]]
-91.14933 -127.34869 72.39871 [[1. 0.]]
-94.3194 -134.99812 81.35745 [[1. 0.]]
3038.6782 -1412.0868 8901.53 [[1. 0.]]
-111.7765 -234.07007 244.58714 [[0. 1.]]
-11

-111.81793 -214.90938 206.18289 [[0. 1.]]
-111.8244 -215.06993 206.49106 [[0. 1.]]
-63.30046 -76.29242 25.983921 [[0. 1.]]
-94.922134 -136.54283 83.2414 [[1.0000000e+00 2.0566773e-16]]
-111.560486 -209.93126 196.74155 [[0. 1.]]
-111.79648 -233.61491 243.63687 [[0. 1.]]
-111.22829 -242.63048 262.80438 [[1.1816345e-34 1.0000000e+00]]
-57.204536 -67.32047 20.231876 [[0. 1.]]
-97.45189 -143.26566 91.62754 [[1. 0.]]
-111.951584 -219.22408 214.54498 [[0. 1.]]
-93.8396 -133.79869 79.91819 [[1. 0.]]
-111.93853 -218.6472 213.41734 [[0. 1.]]
-95.87366 -138.99971 86.2521 [[1. 0.]]
-111.948265 -219.07162 214.24672 [[0. 1.]]
2600.4321 -1326.3658 7853.5957 [[1. 0.]]
-93.79663 -133.69205 79.79083 [[1. 0.]]
-96.94823 -141.8802 89.86395 [[1. 0.]]
-109.77753 -255.57822 291.60138 [[1. 0.]]
-14.324817 -14.814706 0.9797786 [[0. 1.]]
-106.943695 -271.61246 329.33752 [[1. 0.]]
-99.29658 -148.55699 98.52083 [[1. 0.]]
2761.404 -1358.6047 8240.018 [[1. 0.]]
-107.69833 -267.91824 320.43982 [[1. 0.]]
epsilon : 0.

-97.2816 -142.79462 91.02603 [[1. 0.]]
-97.31058 -142.87456 91.12797 [[1. 0.]]
-109.30307 -258.78186 298.95758 [[1. 0.]]
-111.96998 -227.82811 231.71626 [[0. 1.]]
-108.45337 -263.88113 310.85553 [[1. 0.]]
-111.897255 -230.87509 237.95567 [[0. 1.]]
-109.49339 -257.53357 296.08035 [[1. 0.]]
-104.00049 -283.8803 359.75964 [[1. 0.]]
-111.84473 -215.59518 207.50092 [[0. 1.]]
-111.97008 -220.18759 216.43503 [[0. 1.]]
-98.758484 -146.97595 96.434944 [[1. 0.]]
-109.36218 -258.399 298.0736 [[1. 0.]]
-111.57526 -237.8419 252.5333 [[0. 1.]]
2643.2134 -1335.0253 7956.4775 [[1. 0.]]
-111.71086 -235.4378 247.45389 [[0. 1.]]
2520.7283 -1310.0488 7661.554 [[0. 1.]]
-111.726875 -235.11945 246.78514 [[1.0950006e-31 1.0000000e+00]]
-24.910355 -158.78235 267.744 [[3.7270453e-09 1.0000000e+00]]
-96.385315 -140.35889 87.947136 [[1. 0.]]
-110.79693 -200.76393 179.934 [[0. 1.]]
-111.56593 -210.01826 196.90466 [[0. 1.]]
-111.84821 -215.68837 207.68031 [[0. 1.]]
-50.18879 -57.59237 14.807159 [[0. 1.]]
-95.11734

KeyboardInterrupt: 